In [1]:
import numpy as np
import time
import pickle
import os
import matplotlib.pyplot as plt
import warnings
import pandas as pd

warnings.filterwarnings('ignore')

In [2]:
print("----------------Reading the Data-------------------------")
PATH = os.getcwd()
os.chdir('Alphabets/')

X_train = pd.read_csv('train.csv', sep=',', header=None, index_col=False)
X_test = pd.read_csv('test.csv', sep=',', header=None, index_col=False)
np.random.shuffle(X_train.to_numpy())
train_class = X_train[X_train.columns[-1]]
test_actual_class = X_test[X_test.columns[-1]]

X_train = X_train.drop(X_train.columns[-1], axis=1)
X_test = X_test.drop(X_test.columns[-1], axis=1)

print("----------------Data Reading completed-------------------")

os.chdir('../')

X_train = X_train/255
X_test = X_test/255
m = X_train.shape[0] # Number of Training Samples
n = X_train.shape[1] # Number of input features

print("The total number of training samples = {}".format(m))
print("The number of features = {}".format(n))

----------------Reading the Data-------------------------
----------------Data Reading completed-------------------
The total number of training samples = 13000
The number of features = 784


In [3]:
#To get the one hot encoding of each label
print("--------Perform 1-hot encoding of class labels------------")

train_class_enc = pd.get_dummies(train_class).to_numpy()
test_actual_class_enc = pd.get_dummies(test_actual_class).to_numpy()

--------Perform 1-hot encoding of class labels------------


In [4]:
#Add the intercept term to the data samples both in training and test dataset
X_train = np.hstack((np.ones((m,1)),X_train.to_numpy()))
X_test = np.hstack((np.ones((X_test.shape[0],1)),X_test.to_numpy()))

In [5]:
lr = 0.1
arch_test = [1,5,10,50,100] # Only for single layer
arch = [arch_test[3]] #means one hidden layer with #perceptrons 
batch_size = 100 # Mini-Batch Size
r = np.max(train_class) + 1 # Default value of the number of classes = 26

In [6]:
#Mini-Batch formation
mini_batch = [(X_train[i:i+batch_size,:], train_class_enc[i:i+batch_size]) for i in range(0, m, batch_size)]
print("The number of mini-batches formed is = {}".format(len(mini_batch)))

The number of mini-batches formed is = 130


In [7]:
#Theta Initialization 
#np.random.seed(1)
def theta_init(arch=[50]):
    theta = []
    for i in range(len(arch)+1):
        if i == 0:
            dim0=n+1
            dim1=arch[i]
        elif (i == len(arch)):
            dim0=arch[i-1]
            dim1 = r
        else:
            dim0=arch[i-1]
            dim1= arch[i]

        theta.append(2*np.random.random((dim0, dim1))-1)
        #theta.append(np.zeros((dim0, dim1)))
    return theta

In [8]:
def activation(x):
    return 1/(1+np.exp(-x))

In [9]:
def forward_prop(data, theta):
    fm = []
    fm.append(data)
    for l in range(len(theta)):
        fm.append(activation(np.dot(fm[l], theta[l])))
    return fm

In [10]:
def cost_total(X, theta, Y, m):
    fm = forward_prop(X, theta)
    cost = (1/(2*m))*np.sum((Y-fm[-1])**2)
    return cost

In [11]:
def calc_accuracy(data, theta, actual_class):
    pred_class = forward_prop(data, theta)
    test_pred_class = pred_class[-1]
    for i in range(len(test_pred_class)):
        test_pred_class[i][test_pred_class[i] == np.max(test_pred_class[i])] = 1
        test_pred_class[i][test_pred_class[i] != np.max(test_pred_class[i])] = 0


    test_acc = 0
    for i in range(len(actual_class)):
        if (np.array_equal(test_pred_class[i], actual_class[i])):
            test_acc+=1
    test_acc /= data.shape[0]

    #print("The Test Accuracy of the model = {}%".format(test_acc*100))
    return (test_acc*100)

In [29]:
epochs = []
train_accuracy = []
test_accuracy = []
train_time = []

In [30]:
arch_test=[100]
for i in range(len(arch_test)):
    theta = theta_init([arch_test[i]])
    fm = forward_prop(X_train, theta)
    
    epoch = 0
    start = time.time()
    cost_init = cost_total(X_train, theta, train_class_enc, m)

    while(True):
        count = 0

        print("Initial Cost for this epoch {} = {}".format(epoch, cost_init))

        for b in mini_batch:
            X_b = b[0]
            Y_b = b[1]
            fm = forward_prop(X_b, theta)
            delta = [None]*len(fm)

            if (count % 60 == 0):
                print("Error = "+str(cost_total(X_b, theta, Y_b, batch_size)))
            #Backward Propagation

            for l in range(len(fm)-1, 0, -1):
                if (l == len(fm)-1):
                    delta[l] = ((1/batch_size)*(Y_b - fm[l])*fm[l]*(1-fm[l]))
                else:
                    delta[l]=(np.dot(delta[l+1], theta[l].T)*fm[l]*(1-fm[l]))

            #delta_l1 = np.dot(delta_l2, theta2.T)*l1*(1-l1)

            for t in range(len(theta)):
                theta[t] += lr*np.dot(fm[t].T, delta[t+1]) 

            count+=1
        epoch+=1 #Number of epochs
        cost_final = cost_total(X_train, theta, train_class_enc, m)
        print("Cost after {} epochs is = {}".format(epoch, cost_final))
        if (abs(cost_final-cost_init) < 1e-07):
            print("cost initial= {} , cost final={} , change in cost= {}".format(cost_init,cost_final, cost_final-cost_init))
            break
        cost_init = cost_final
    epochs.append(epoch)
    train_time.append(time.time()-start)
    train_accuracy.append(calc_accuracy(X_train, theta, train_class_enc))
    test_accuracy.append(calc_accuracy(X_test, theta, test_actual_class_enc))
    print("\n------------------------------------------------------------------------------")
    print("The stats for number of units in the hidden layer = {} are as below:".format(arch_test[i]))
    print("------------------------------------------------------------------------------")
    print("The number of epochs = {}".format(epochs[-1]))
    print("The training time = {}sec".format(train_time[-1]))
    print("The training accuracy is = {}%".format(train_accuracy[-1]))
    print("The test accuracy is = {}%".format(test_accuracy[-1]))
    print("------------------------------------------------------------------------------\n")

Initial Cost for this epoch 0 = 3.7027668040901247
Error = 3.757407761885104
Error = 0.75107620612236
Error = 0.5280118761009039
Cost after 1 epochs is = 0.5310321398713069
Initial Cost for this epoch 1 = 0.5310321398713069
Error = 0.5342819117676538
Error = 0.5232128308631939
Error = 0.4992108213103491
Cost after 2 epochs is = 0.5014558267705163
Initial Cost for this epoch 2 = 0.5014558267705163
Error = 0.5026002138008541
Error = 0.5066402469892007
Error = 0.49364810615961957
Cost after 3 epochs is = 0.49485721964623935
Initial Cost for this epoch 3 = 0.49485721964623935
Error = 0.4954615000173461
Error = 0.501031813096512
Error = 0.49129975321053837
Cost after 4 epochs is = 0.4919070587814294
Initial Cost for this epoch 4 = 0.4919070587814294
Error = 0.49226628049876087
Error = 0.4981424164028763
Error = 0.4897952521504211
Cost after 5 epochs is = 0.4900351582422922
Initial Cost for this epoch 5 = 0.4900351582422922
Error = 0.49025276567513965
Error = 0.4962819091028166
Error = 0.488

Error = 0.40156286906069105
Cost after 48 epochs is = 0.40615982270097
Initial Cost for this epoch 48 = 0.40615982270097
Error = 0.38925808524108485
Error = 0.4173505278764584
Error = 0.3992609368823432
Cost after 49 epochs is = 0.40432967029415423
Initial Cost for this epoch 49 = 0.40432967029415423
Error = 0.3875181514362718
Error = 0.41511187483576445
Error = 0.39695411972315897
Cost after 50 epochs is = 0.402495098494375
Initial Cost for this epoch 50 = 0.402495098494375
Error = 0.38578599532546587
Error = 0.4128723299945442
Error = 0.3946392529486812
Cost after 51 epochs is = 0.400651564451346
Initial Cost for this epoch 51 = 0.400651564451346
Error = 0.3840552686832993
Error = 0.41063095637251734
Error = 0.3923107998992822
Cost after 52 epochs is = 0.39879426054045625
Initial Cost for this epoch 52 = 0.39879426054045625
Error = 0.3823188016335547
Error = 0.4083868734151555
Error = 0.38996116546076864
Cost after 53 epochs is = 0.39691829781774896
Initial Cost for this epoch 53 = 0

Error = 0.34176965247483987
Error = 0.3081206925764799
Cost after 95 epochs is = 0.32486854577355373
Initial Cost for this epoch 95 = 0.32486854577355373
Error = 0.3064696654000889
Error = 0.3407646684981455
Error = 0.3068817039647089
Cost after 96 epochs is = 0.323647779079394
Initial Cost for this epoch 96 = 0.323647779079394
Error = 0.3051274282459787
Error = 0.33976918057302113
Error = 0.3056618502640252
Cost after 97 epochs is = 0.32244025463122317
Initial Cost for this epoch 97 = 0.32244025463122317
Error = 0.30379011194484856
Error = 0.3387822594955027
Error = 0.30445994468157206
Cost after 98 epochs is = 0.321244814886335
Initial Cost for this epoch 98 = 0.321244814886335
Error = 0.3024565997491918
Error = 0.3378029344434208
Error = 0.30327479109290395
Cost after 99 epochs is = 0.3200602835969235
Initial Cost for this epoch 99 = 0.3200602835969235
Error = 0.30112605504938794
Error = 0.3368301733304223
Error = 0.3021052295631165
Cost after 100 epochs is = 0.31888546683216457
Ini

Cost after 140 epochs is = 0.2725137168531327
Initial Cost for this epoch 140 = 0.2725137168531327
Error = 0.25436613273587705
Error = 0.3008293320964691
Error = 0.2652128436430905
Cost after 141 epochs is = 0.271560490676871
Initial Cost for this epoch 141 = 0.271560490676871
Error = 0.2534901171774056
Error = 0.3001874161153653
Error = 0.26455247485827676
Cost after 142 epochs is = 0.27062733714404863
Initial Cost for this epoch 142 = 0.27062733714404863
Error = 0.25263142015481643
Error = 0.29955103764388363
Error = 0.26390166637880863
Cost after 143 epochs is = 0.26971331258161635
Initial Cost for this epoch 143 = 0.26971331258161635
Error = 0.2517895693562017
Error = 0.298919944255115
Error = 0.2632595031481989
Cost after 144 epochs is = 0.26881750477647814
Initial Cost for this epoch 144 = 0.26881750477647814
Error = 0.2509640507783757
Error = 0.29829386883006026
Error = 0.26262514372319146
Cost after 145 epochs is = 0.26793904647266953
Initial Cost for this epoch 145 = 0.2679390

Cost after 186 epochs is = 0.24135056438644462
Initial Cost for this epoch 186 = 0.24135056438644462
Error = 0.22571897762065
Error = 0.2747003715693421
Error = 0.24003637585142848
Cost after 187 epochs is = 0.24085385457006503
Initial Cost for this epoch 187 = 0.24085385457006503
Error = 0.2252609341181239
Error = 0.27420874877098395
Error = 0.23959021467150685
Cost after 188 epochs is = 0.24036139495290415
Initial Cost for this epoch 188 = 0.24036139495290415
Error = 0.22480659819309046
Error = 0.27372041815761045
Error = 0.23914801658400314
Cost after 189 epochs is = 0.23987295420760418
Initial Cost for this epoch 189 = 0.23987295420760418
Error = 0.22435573370384698
Error = 0.27323518670961955
Error = 0.2387097278180473
Cost after 190 epochs is = 0.2393882857894698
Initial Cost for this epoch 190 = 0.2393882857894698
Error = 0.22390808642980795
Error = 0.2727528235780296
Error = 0.23827529978111023
Cost after 191 epochs is = 0.2389071237363816
Initial Cost for this epoch 191 = 0.23

...

Error = 0.011332312772943146
Error = 0.016056709451838142
Cost after 25006 epochs is = 0.0180490539586971
Initial Cost for this epoch 25006 = 0.0180490539586971
Error = 0.02553027824601567
Error = 0.011332234311283319
Error = 0.01605663036861171
Cost after 25007 epochs is = 0.01804893965208625
Initial Cost for this epoch 25007 = 0.01804893965208625
Error = 0.025530260625658607
Error = 0.01133215605497947
Error = 0.01605655112648168
Cost after 25008 epochs is = 0.01804882544348562
Initial Cost for this epoch 25008 = 0.01804882544348562
Error = 0.02553024305532351
Error = 0.011332078002851494
Error = 0.016056471726056006
Cost after 25009 epochs is = 0.018048711332917702
Initial Cost for this epoch 25009 = 0.018048711332917702
Error = 0.02553022553405258
Error = 0.011332000153712683
Error = 0.016056392167958716
Cost after 25010 epochs is = 0.01804859732039634
Initial Cost for this epoch 25010 = 0.01804859732039634
Error = 0.025530208060895978
Error = 0.011331922506369963
Error = 0.0160563

Error = 0.011329109231737949
Error = 0.01605317457169005
Cost after 25049 epochs is = 0.018044226604471934
Initial Cost for this epoch 25049 = 0.018044226604471934
Error = 0.025529554910876384
Error = 0.011329038485282817
Error = 0.01605308936508994
Cost after 25050 epochs is = 0.01804411644068207
Initial Cost for this epoch 25050 = 0.01804411644068207
Error = 0.025529538675493874
Error = 0.011328967890625477
Error = 0.016053004036505693
Cost after 25051 epochs is = 0.018044006369520017
Initial Cost for this epoch 25051 = 0.018044006369520017
Error = 0.025529522456152788
Error = 0.011328897446525201
Error = 0.01605291858696942
Cost after 25052 epochs is = 0.018043896390740718
Initial Cost for this epoch 25052 = 0.018043896390740718
Error = 0.025529506252233027
Error = 0.011328827151744538
Error = 0.016052833017517348
Cost after 25053 epochs is = 0.01804378650409517
Initial Cost for this epoch 25053 = 0.01804378650409517
Error = 0.025529490063121787
Error = 0.011328757005049485
Error = 

Error = 0.01132618944942627
Error = 0.01604941357889697
Cost after 25092 epochs is = 0.018039569772558932
Initial Cost for this epoch 25092 = 0.018039569772558932
Error = 0.025528864475867896
Error = 0.011326124168933952
Error = 0.016049324084579028
Cost after 25093 epochs is = 0.018039463331730354
Initial Cost for this epoch 25093 = 0.018039463331730354
Error = 0.025528848454424553
Error = 0.011326058991627324
Error = 0.01604923451396086
Cost after 25094 epochs is = 0.018039356970391295
Initial Cost for this epoch 25094 = 0.018039356970391295
Error = 0.02552883242835797
Error = 0.01132599391652743
Error = 0.01604914486808674
Cost after 25095 epochs is = 0.01803925068819359
Initial Cost for this epoch 25095 = 0.01803925068819359
Error = 0.025528816397318944
Error = 0.01132592894266348
Error = 0.016049055147998238
Cost after 25096 epochs is = 0.018039144484787988
Initial Cost for this epoch 25096 = 0.018039144484787988
Error = 0.02552880036096356
Error = 0.011325864069072935
Error = 0.0

Cost after 25135 epochs is = 0.018035060196852214
Initial Cost for this epoch 25135 = 0.018035060196852214
Error = 0.02552816767842372
Error = 0.011323402914117034
Error = 0.016045417029646517
Cost after 25136 epochs is = 0.0180349568503048
Initial Cost for this epoch 25136 = 0.0180349568503048
Error = 0.02552815120261763
Error = 0.011323341361633892
Error = 0.016045325120307475
Cost after 25137 epochs is = 0.018034853567688507
Initial Cost for this epoch 25137 = 0.018034853567688507
Error = 0.025528134711411746
Error = 0.011323279877496165
Error = 0.016045233177156958
Cost after 25138 epochs is = 0.018034750348635623
Initial Cost for this epoch 25138 = 0.018034750348635623
Error = 0.02552811820464643
Error = 0.011323218461114386
Error = 0.016045141201063137
Cost after 25139 epochs is = 0.018034647192778478
Initial Cost for this epoch 25139 = 0.018034647192778478
Error = 0.025528101682165637
Error = 0.011323157111908167
Error = 0.01604504919288945
Cost after 25140 epochs is = 0.0180345

Cost after 25179 epochs is = 0.01803056857242044
Initial Cost for this epoch 25179 = 0.01803056857242044
Error = 0.025527426517449336
Error = 0.0113207526650986
Error = 0.016041351889352455
Cost after 25180 epochs is = 0.018030467692645432
Initial Cost for this epoch 25180 = 0.018030467692645432
Error = 0.025527409256795242
Error = 0.011320693679865266
Error = 0.01604125925119033
Cost after 25181 epochs is = 0.018030366860762464
Initial Cost for this epoch 25181 = 0.018030366860762464
Error = 0.025527391976748623
Error = 0.011320634745370763
Error = 0.016041166612992475
Cost after 25182 epochs is = 0.018030266076411866
Initial Cost for this epoch 25182 = 0.018030266076411866
Error = 0.025527374677282447
Error = 0.011320575861405256
Error = 0.01604107397542572
Cost after 25183 epochs is = 0.01803016533923418
Initial Cost for this epoch 25183 = 0.01803016533923418
Error = 0.025527357358372235
Error = 0.011320517027766952
Error = 0.016040981339152733
Cost after 25184 epochs is = 0.0180300

In [31]:
epochs

[25200]